In [1]:
pip install learnergy

Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install torch

Note: you may need to restart the kernel to use updated packages.


In [3]:
import torchvision as torchv
import torch
import numpy as np 
import pandas as pd 
import os
from sklearn.model_selection import train_test_split
from learnergy.models.gaussian import GaussianRBM
from learnergy.core.dataset import Dataset
from IPython.display import HTML
import tensorflow as tf
from sklearn.metrics import accuracy_score, precision_score, recall_score

valores=[["MSE", "PL", 'RMSE', 'PV']]

In [5]:
def predict(loss, reconstructions, threshold, data):
    loss = tf.keras.losses.mse(reconstructions, data)
    return tf.math.less(loss, threshold)

def print_stats(predictions, labels):
    print("Accuracy = {}".format(accuracy_score(labels, predictions)))
    print("Precision = {}".format(precision_score(labels, predictions)))
    print("Recall = {}".format(recall_score(labels, predictions)))

In [6]:
# Criar os modelos de RBM
# Comparar quantidades de hidden layers
# Dados já estão normalizados
model400 = GaussianRBM(
    n_visible=41,
    n_hidden=400,
    steps=1,
    learning_rate=0.01,
    momentum=0,
    decay=0,
    use_gpu=False,
    normalize=False,
    input_normalize=False,
)

model200 = GaussianRBM(
    n_visible=41,
    n_hidden=200,
    steps=1,
    learning_rate=0.01,
    momentum=0,
    decay=0,
    use_gpu=False,
    normalize=False,
    input_normalize=False,
)

2023-01-02 16:47:35,244 - learnergy.models.gaussian.gaussian_rbm — INFO — Overriding class: RBM -> GaussianRBM.
2023-01-02 16:47:35,247 - learnergy.models.bernoulli.rbm — INFO — Overriding class: Model -> RBM.
2023-01-02 16:47:35,345 - learnergy.core.model — DEBUG — Device: cpu.
2023-01-02 16:47:35,347 - learnergy.models.bernoulli.rbm — INFO — Class overrided.
2023-01-02 16:47:35,349 - learnergy.models.bernoulli.rbm — DEBUG — Size: (41, 400) | Learning: CD-1 | Hyperparameters: lr = 0.01, momentum = 0, decay = 0, T = 1.0.
2023-01-02 16:47:35,350 - learnergy.models.gaussian.gaussian_rbm — INFO — Class overrided.
2023-01-02 16:47:35,351 - learnergy.models.gaussian.gaussian_rbm — INFO — Overriding class: RBM -> GaussianRBM.
2023-01-02 16:47:35,352 - learnergy.models.bernoulli.rbm — INFO — Overriding class: Model -> RBM.
2023-01-02 16:47:35,354 - learnergy.core.model — DEBUG — Device: cpu.
2023-01-02 16:47:35,355 - learnergy.models.bernoulli.rbm — INFO — Class overrided.
2023-01-02 16:47:35

In [ ]:
#CARREGAR KDD99 - 400 - MINMAX
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

#carregar os dados 
dataframe1 = pd.read_csv("/kaggle/input/kdd99400mm/data400kddDICMinMax.csv", header=None)

#pegar valores da dataframe
raw_data1 = dataframe1.values
dataframe1.head()

# Separar labels
labels1 = raw_data1[1:, -1]

# Separar valores
data1 = raw_data1[1:, 0:41]

# Dividir os dados nos sets
train_data1, test_data1, train_labels1, test_labels1 = train_test_split(
        data1, labels1, test_size=0.2, random_state=21
)

# Transformar valores de texto para número
train_labels1 = np.float32(train_labels1)
test_labels1 = np.float32(test_labels1)
test_data1 = np.float32(test_data1)
train_labelsb1 = train_labels1.astype(bool)
test_labelsb1 = test_labels1.astype(bool)
normal_train_data1 = np.float32(train_data1[~train_labelsb1]) #dados (false) normais (0)
normal_test_data1 = np.float32(test_data1[~test_labelsb1])
anomalous_train_data1 = np.float32(train_data1[train_labelsb1]) #dados (true) anomalos (1)
anomalous_test_data1 = np.float32(test_data1[test_labelsb1])
normal_train_labels1 = np.float32(train_labels1[~train_labelsb1])

dataset1=Dataset(normal_train_data1, normal_train_labels1)
teste1=Dataset(test_data1, test_labels1)

In [ ]:
valores.append(["kdd400MinMax"])
for x in range(10):
    mse11, pl11 = model400.fit(dataset1, batch_size=50, epochs=50)
    train_loss11, recoProb11 = model400.reconstruct(teste1)
    threshold11 = np.mean(train_loss11.detach().numpy()) + np.std(train_loss11.detach().numpy())
    print("Threshold: ", threshold11)
    reconstructions11 = torch.bernoulli(recoProb11)
    preds11 = predict(train_loss11.detach().numpy(), reconstructions11.detach().numpy(), threshold11, test_data1)
    print_stats(preds11.numpy(), test_labels1)
    valores.append([threshold11, format(accuracy_score(preds11, test_labels1.astype(float))), format(precision_score(preds11, test_labels1.astype(float))), format(recall_score(preds11, test_labels1.astype(float)))])
    

for x in range(10):
    mse12, pl12 = model200.fit(dataset1, batch_size=50, epochs=50)
    train_loss12, recoProb12 = model400.reconstruct(teste1)
    threshold12 = np.mean(train_loss12.detach().numpy()) + np.std(train_loss12.detach().numpy())
    print("Threshold: ", threshold12)
    reconstructions12 = torch.bernoulli(recoProb12)
    preds12 = predict(train_loss12.detach().numpy(), reconstructions12.detach().numpy(), threshold12, test_data1)
    print_stats(preds12.numpy(), test_labels1) 
    valores.append([threshold12, format(accuracy_score(preds12, test_labels1.astype(float))), format(precision_score(preds12, test_labels1.astype(float))), format(recall_score(preds12, test_labels1.astype(float)))])
    

for x in range(10):
    mse13, pl13 = model400.fit(dataset1, batch_size=10, epochs=50)
    train_loss13, recoProb13 = model400.reconstruct(teste1)
    threshold13 = np.mean(train_loss13.detach().numpy()) + np.std(train_loss13.detach().numpy())
    print("Threshold: ", threshold13)
    reconstructions13 = torch.bernoulli(recoProb13)
    preds13 = predict(train_loss13.detach().numpy(), reconstructions13.detach().numpy(), threshold13, test_data1)
    print_stats(preds13.numpy(), test_labels1) 
    valores.append([threshold12, format(accuracy_score(preds13, test_labels1.astype(float))), format(precision_score(preds13, test_labels1.astype(float))), format(recall_score(preds13, test_labels1.astype(float)))])
    
    
for x in range(10):
    mse14, pl14 = model200.fit(dataset1, batch_size=10, epochs=50)
    train_loss14, recoProb14 = model400.reconstruct(teste1)
    threshold14 = np.mean(train_loss14.detach().numpy()) + np.std(train_loss14.detach().numpy())
    print("Threshold: ", threshold14)
    reconstructions14 = torch.bernoulli(recoProb14)
    preds14 = predict(train_loss14.detach().numpy(), reconstructions14.detach().numpy(), threshold14, test_data1)
    print_stats(preds14.numpy(), test_labels1) 
    valores.append([threshold14, format(accuracy_score(preds14, test_labels1.astype(float))), format(precision_score(preds14, test_labels1.astype(float))), format(recall_score(preds14, test_labels1.astype(float)))])
    
    
for x in range(10):
    mse15, pl15 = model400.fit(dataset1, batch_size=10, epochs=100)
    train_loss15, recoProb15 = model400.reconstruct(teste1)
    threshold15 = np.mean(train_loss15.detach().numpy()) + np.std(train_loss15.detach().numpy())
    print("Threshold: ", threshold15)
    reconstructions15 = torch.bernoulli(recoProb15)
    preds15 = predict(train_loss15.detach().numpy(), reconstructions15.detach().numpy(), threshold15, test_data1)
    print_stats(preds15.numpy(), test_labels1) 
    valores.append([threshold15, format(accuracy_score(preds15, test_labels1.astype(float))), format(precision_score(preds15, test_labels1.astype(float))), format(recall_score(preds15, test_labels1.astype(float)))])
    
for x in range(10):
    mse16, pl16 = model200.fit(dataset1, batch_size=10, epochs=100)
    train_loss16, recoProb16 = model400.reconstruct(teste1)
    threshold16 = np.mean(train_loss16.detach().numpy()) + np.std(train_loss16.detach().numpy())
    print("Threshold: ", threshold16)
    reconstructions16 = torch.bernoulli(recoProb16)
    preds16 = predict(train_loss16.detach().numpy(), reconstructions16.detach().numpy(), threshold16, test_data1)
    print_stats(preds16.numpy(), test_labels1) 
    valores.append([threshold16, format(accuracy_score(preds16, test_labels1.astype(float))), format(precision_score(preds16, test_labels1.astype(float))), format(recall_score(preds16, test_labels1.astype(float)))])

df = pd.DataFrame(valores) 
df.to_csv('resultRBM400mm.csv',index=False)

def create_download_link(title = "Download CSV file", filename = "data.csv"):  
    html = '<a href={filename}>{title}</a>'
    html = html.format(title=title,filename=filename)
    return HTML(html)

# create a link to download the dataframe which was saved with .to_csv method
create_download_link(filename='resultRBM400mm.csv')

In [ ]:
#CARREGAR KDD99 - 400 - NORMALIZE
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

#carregar os dados 
dataframe2 = pd.read_csv("/kaggle/input/kdd99400norm/data400kddDICnormalized.csv", header=None)

#pegar valores da dataframe
raw_data2 = dataframe2.values
dataframe2.head()

# Separar labels
labels2 = raw_data2[1:, -1]

# Separar valores
data2 = raw_data2[1:, 0:41]

# Dividir os dados nos sets
train_data2, test_data2, train_labels2, test_labels2 = train_test_split(
        data2, labels2, test_size=0.2, random_state=21
)

# Transformar valores de texto para número
train_labels2 = np.float32(train_labels2)
test_labels2 = np.float32(test_labels2)
test_data2 = np.float32(test_data2)
train_labelsb2 = train_labels2.astype(bool)
test_labelsb2 = test_labels2.astype(bool)
normal_train_data2 = np.float32(train_data2[~train_labelsb2]) #dados (false) normais (0)
normal_test_data2 = np.float32(test_data2[~test_labelsb2])
anomalous_train_data2 = np.float32(train_data2[train_labelsb2]) #dados (true) anomalos (1)
anomalous_test_data2 = np.float32(test_data2[test_labelsb2])
normal_train_labels2 = np.float32(train_labels2[~train_labelsb2])

dataset2=Dataset(normal_train_data2, normal_train_labels2)
teste2=Dataset(test_data2, test_labels2)

In [ ]:
valores=[["MSE", "PL", 'RMSE', 'PV']]
valores.append(["kdd400Normal"])

for x in range(10):
    mse21, pl21 = model400.fit(dataset2, batch_size=50, epochs=50)
    train_loss21, recoProb21 = model400.reconstruct(teste2)
    threshold21 = np.mean(train_loss21.detach().numpy()) + np.std(train_loss21.detach().numpy())
    print("Threshold: ", threshold21)
    reconstructions21 = torch.bernoulli(recoProb21)
    preds21 = predict(train_loss21.detach().numpy(), reconstructions21.detach().numpy(), threshold21, test_data2)
    print_stats(preds21.numpy(), test_labelsb2)
    valores.append([threshold21, format(accuracy_score(preds21.numpy(), test_labelsb2)), format(precision_score(preds21.numpy(), test_labelsb2)), format(recall_score(preds21.numpy(), test_labelsb2))])
    
for x in range(10):
    mse22, pl22 = model200.fit(dataset2, batch_size=50, epochs=50)
    train_loss22, recoProb22 = model400.reconstruct(teste2)
    threshold22 = np.mean(train_loss22.detach().numpy()) + np.std(train_loss22.detach().numpy())
    print("Threshold: ", threshold22)
    reconstructions22 = torch.bernoulli(recoProb22)
    preds22 = predict(train_loss22.detach().numpy(), reconstructions22.detach().numpy(), threshold22, test_data2)
    print_stats(preds22.numpy(), test_labelsb2) 
    valores.append([threshold22, format(accuracy_score(preds22.numpy(), test_labelsb2)), format(precision_score(preds22.numpy(), test_labelsb2)), format(recall_score(preds22.numpy(), test_labelsb2))])
    
for x in range(10):
    mse23, pl23 = model400.fit(dataset2, batch_size=10, epochs=50)
    train_loss23, recoProb23 = model400.reconstruct(teste2)
    threshold23 = np.mean(train_loss23.detach().numpy()) + np.std(train_loss23.detach().numpy())
    print("Threshold: ", threshold23)
    reconstructions23 = torch.bernoulli(recoProb23)
    preds23 = predict(train_loss23.detach().numpy(), reconstructions23.detach().numpy(), threshold23, test_data2)
    print_stats(preds23.numpy(), test_labelsb2) 
    valores.append([threshold23, format(accuracy_score(preds23.numpy(), test_labelsb2)), format(precision_score(preds23.numpy(), test_labelsb2)), format(recall_score(preds23.numpy(), test_labelsb2))])
    
for x in range(10):
    mse24, pl24 = model200.fit(dataset2, batch_size=10, epochs=50)
    train_loss24, recoProb24 = model400.reconstruct(teste2)
    threshold24 = np.mean(train_loss24.detach().numpy()) + np.std(train_loss24.detach().numpy())
    print("Threshold: ", threshold24)
    reconstructions24 = torch.bernoulli(recoProb24)
    preds24 = predict(train_loss24.detach().numpy(), reconstructions24.detach().numpy(), threshold24, test_data2)
    print_stats(preds24.numpy(), test_labelsb2) 
    valores.append([threshold24, format(accuracy_score(preds24.numpy(), test_labelsb2)), format(precision_score(preds24.numpy(), test_labelsb2)), format(recall_score(preds24.numpy(), test_labelsb2))])
    
for x in range(10):
    mse25, pl25 = model400.fit(dataset2, batch_size=10, epochs=100)
    train_loss25, recoProb25 = model400.reconstruct(teste2)
    threshold25 = np.mean(train_loss25.detach().numpy()) + np.std(train_loss25.detach().numpy())
    print("Threshold: ", threshold25)
    reconstructions25 = torch.bernoulli(recoProb25)
    preds25 = predict(train_loss25.detach().numpy(), reconstructions25.detach().numpy(), threshold25, test_data2)
    print_stats(preds25.numpy(), test_labelsb2) 
    valores.append([threshold25, format(accuracy_score(preds25.numpy(), test_labelsb2)), format(precision_score(preds25.numpy(), test_labelsb2)), format(recall_score(preds25.numpy(), test_labelsb2))])
    
for x in range(10):
    mse26, pl26 = model200.fit(dataset2, batch_size=10, epochs=100)
    train_loss26, recoProb26 = model400.reconstruct(teste2)
    threshold26 = np.mean(train_loss26.detach().numpy()) + np.std(train_loss26.detach().numpy())
    print("Threshold: ", threshold26)
    reconstructions26 = torch.bernoulli(recoProb26)
    preds26 = predict(train_loss26.detach().numpy(), reconstructions26.detach().numpy(), threshold26, test_data2)
    print_stats(preds26.numpy(), test_labelsb2) 
    valores.append([threshold26, format(accuracy_score(preds26.numpy(), test_labelsb2)), format(precision_score(preds26.numpy(), test_labelsb2)), format(recall_score(preds26.numpy(), test_labelsb2))])

df = pd.DataFrame(valores) 
df.to_csv('resultRBM400norm.csv',index=False)

def create_download_link(title = "Download CSV file", filename = "data.csv"):  
    html = '<a href={filename}>{title}</a>'
    html = html.format(title=title,filename=filename)
    return HTML(html)

# create a link to download the dataframe which was saved with .to_csv method
create_download_link(filename='resultRBM400norm.csv')

In [ ]:
#CARREGAR KDD99 - 800 - MINMAX
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

#carregar os dados 
dataframe3 = pd.read_csv("/kaggle/input/kdd99800mm/data800kddDICMinMax.csv", header=None)

#pegar valores da dataframe
raw_data3 = dataframe3.values
dataframe3.head()

# Separar labels
labels3 = raw_data3[1:, -1]

# Separar valores
data3 = raw_data3[1:, 0:41]

# Dividir os dados nos sets
train_data3, test_data3, train_labels3, test_labels3 = train_test_split(
        data3, labels3, test_size=0.2, random_state=21
)

# Transformar valores de texto para número
train_labels3 = np.float32(train_labels3)
test_labels3 = np.float32(test_labels3)
test_data3 = np.float32(test_data3)
train_labelsb3 = train_labels3.astype(bool)
test_labelsb3 = test_labels3.astype(bool)
normal_train_data3 = np.float32(train_data3[~train_labelsb3]) #dados (false) normais (0)
normal_test_data3 = np.float32(test_data3[~test_labelsb3])
anomalous_train_data3 = np.float32(train_data3[train_labelsb3]) #dados (true) anomalos (1)
anomalous_test_data3 = np.float32(test_data3[test_labelsb3])
normal_train_labels3 = np.float32(train_labels3[~train_labelsb3])

dataset3=Dataset(normal_train_data3, normal_train_labels3)
teste3=Dataset(test_data3, test_labels3)

In [ ]:
valores=[["MSE", "PL", 'RMSE', 'PV']]
valores.append(["kdd800MinMax"])
for x in range(10):
    mse31, pl31 = model400.fit(dataset3, batch_size=50, epochs=50)
    train_loss31, recoProb31 = model400.reconstruct(teste3)
    threshold31 = np.mean(train_loss31.detach().numpy()) + np.std(train_loss31.detach().numpy())
    print("Threshold: ", threshold31)
    reconstructions31 = torch.bernoulli(recoProb31)
    preds31 = predict(train_loss31.detach().numpy(), reconstructions31.detach().numpy(), threshold31, test_data3)
    print_stats(preds31.numpy(), test_labelsb3) 
    valores.append([threshold31, format(accuracy_score(preds31.numpy(), test_labelsb3)), format(precision_score(preds31.numpy(), test_labelsb3)), format(recall_score(preds31.numpy(), test_labelsb3))])
    
for x in range(10):
    mse32, pl32 = model200.fit(dataset3, batch_size=50, epochs=50)
    train_loss32, recoProb32 = model400.reconstruct(teste3)
    threshold32 = np.mean(train_loss32.detach().numpy()) + np.std(train_loss32.detach().numpy())
    print("Threshold: ", threshold32)
    reconstructions32 = torch.bernoulli(recoProb32)
    preds32 = predict(train_loss32.detach().numpy(), reconstructions32.detach().numpy(), threshold32, test_data3)
    print_stats(preds32.numpy(), test_labelsb3) 
    valores.append([threshold32, format(accuracy_score(preds32.numpy(), test_labelsb3)), format(precision_score(preds32.numpy(), test_labelsb3)), format(recall_score(preds32.numpy(), test_labelsb3))])
    
for x in range(10):
    mse33, pl33 = model400.fit(dataset3, batch_size=10, epochs=50)
    train_loss33, recoProb33 = model400.reconstruct(teste3)
    threshold33 = np.mean(train_loss33.detach().numpy()) + np.std(train_loss33.detach().numpy())
    print("Threshold: ", threshold33)
    reconstructions33 = torch.bernoulli(recoProb33)
    preds33 = predict(train_loss33.detach().numpy(), reconstructions33.detach().numpy(), threshold33, test_data3)
    print_stats(preds33.numpy(), test_labelsb3) 
    valores.append([threshold33, format(accuracy_score(preds33.numpy(), test_labelsb3)), format(precision_score(preds33.numpy(), test_labelsb3)), format(recall_score(preds33.numpy(), test_labelsb3))])
    
for x in range(10):
    mse34, pl34 = model200.fit(dataset3, batch_size=10, epochs=50)
    train_loss34, recoProb34 = model400.reconstruct(teste3)
    threshold34 = np.mean(train_loss34.detach().numpy()) + np.std(train_loss34.detach().numpy())
    print("Threshold: ", threshold34)
    reconstructions34 = torch.bernoulli(recoProb34)
    preds34 = predict(train_loss34.detach().numpy(), reconstructions34.detach().numpy(), threshold34, test_data3)
    print_stats(preds34.numpy(), test_labelsb3) 
    valores.append([threshold34, format(accuracy_score(preds34.numpy(), test_labelsb3)), format(precision_score(preds34.numpy(), test_labelsb3)), format(recall_score(preds34.numpy(), test_labelsb3))])
    
for x in range(10):
    mse35, pl35 = model400.fit(dataset3, batch_size=10, epochs=100)
    train_loss35, recoProb35 = model400.reconstruct(teste3)
    threshold35 = np.mean(train_loss35.detach().numpy()) + np.std(train_loss35.detach().numpy())
    print("Threshold: ", threshold35)
    reconstructions35 = torch.bernoulli(recoProb35)
    preds35 = predict(train_loss35.detach().numpy(), reconstructions35.detach().numpy(), threshold35, test_data3)
    print_stats(preds35.numpy(), test_labelsb3) 
    valores.append([threshold35, format(accuracy_score(preds35.numpy(), test_labelsb3)), format(precision_score(preds35.numpy(), test_labelsb3)), format(recall_score(preds35.numpy(), test_labelsb3))])
    
for x in range(10):
    mse36, pl36 = model200.fit(dataset3, batch_size=10, epochs=100)
    train_loss36, recoProb36 = model400.reconstruct(teste3)
    threshold36 = np.mean(train_loss36.detach().numpy()) + np.std(train_loss36.detach().numpy())
    print("Threshold: ", threshold36)
    reconstructions36 = torch.bernoulli(recoProb36)
    preds36 = predict(train_loss36.detach().numpy(), reconstructions36.detach().numpy(), threshold36, test_data3)
    print_stats(preds36.numpy(), test_labelsb3) 
    valores.append([threshold36, format(accuracy_score(preds36.numpy(), test_labelsb3)), format(precision_score(preds36.numpy(), test_labelsb3)), format(recall_score(preds36.numpy(), test_labelsb3))])

df = pd.DataFrame(valores) 
df.to_csv('resultRBM800mm.csv',index=False)

def create_download_link(title = "Download CSV file", filename = "data.csv"):  
    html = '<a href={filename}>{title}</a>'
    html = html.format(title=title,filename=filename)
    return HTML(html)

# create a link to download the dataframe which was saved with .to_csv method
create_download_link(filename='resultRBM800mm.csv')

In [ ]:
#CARREGAR KDD99 - 800 - NORMALIZE
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

#carregar os dados 
dataframe4 = pd.read_csv("/kaggle/input/kdd99800norm/data800kddDICnormalized.csv", header=None)

#pegar valores da dataframe
raw_data4 = dataframe4.values
dataframe4.head()

# Separar labels
labels4 = raw_data4[1:, -1]

# Separar valores
data4 = raw_data4[1:, 0:41]

# Dividir os dados nos sets
train_data4, test_data4, train_labels4, test_labels4 = train_test_split(
        data4, labels4, test_size=0.2, random_state=21
)

# Transformar valores de texto para número
train_labels4 = np.float32(train_labels4)
test_labels4 = np.float32(test_labels4)
test_data4 = np.float32(test_data4)
train_labelsb4 = train_labels4.astype(bool)
test_labelsb4 = test_labels4.astype(bool)
normal_train_data4 = np.float32(train_data4[~train_labelsb4]) #dados (false) normais (0)
normal_test_data4 = np.float32(test_data4[~test_labelsb4])
anomalous_train_data4 = np.float32(train_data4[train_labelsb4]) #dados (true) anomalos (1)
anomalous_test_data4 = np.float32(test_data4[test_labelsb4])
normal_train_labels4 = np.float32(train_labels4[~train_labelsb4])

dataset4=Dataset(normal_train_data4, normal_train_labels4)
teste4=Dataset(test_data4, test_labels4)

In [ ]:
valores=[["MSE", "PL", 'RMSE', 'PV']]
valores.append(["kdd800Normal"])
for x in range(10):
    mse41, pl41 = model400.fit(dataset4, batch_size=50, epochs=50)
    train_loss41, recoProb41 = model400.reconstruct(teste4)
    threshold41 = np.mean(train_loss41.detach().numpy()) + np.std(train_loss41.detach().numpy())
    print("Threshold: ", threshold41)
    reconstructions41 = torch.bernoulli(recoProb41)
    preds41 = predict(train_loss41.detach().numpy(), reconstructions41.detach().numpy(), threshold41, test_data4)
    print_stats(preds41.numpy(), test_labelsb4) 
    valores.append([threshold41, format(accuracy_score(preds41.numpy(), test_labelsb4)), format(precision_score(preds41.numpy(), test_labelsb4)), format(recall_score(preds41.numpy(), test_labelsb4))])
    
for x in range(10):
    mse42, pl42 = model200.fit(dataset4, batch_size=50, epochs=50)
    train_loss42, recoProb42 = model400.reconstruct(teste4)
    threshold42 = np.mean(train_loss42.detach().numpy()) + np.std(train_loss42.detach().numpy())
    print("Threshold: ", threshold42)
    reconstructions42 = torch.bernoulli(recoProb42)
    preds42 = predict(train_loss42.detach().numpy(), reconstructions42.detach().numpy(), threshold42, test_data4)
    print_stats(preds42.numpy(), test_labelsb4) 
    valores.append([threshold42, format(accuracy_score(preds42.numpy(), test_labelsb4)), format(precision_score(preds42.numpy(), test_labelsb4)), format(recall_score(preds42.numpy(), test_labelsb4))])
    
for x in range(10):
    mse43, pl43 = model400.fit(dataset4, batch_size=10, epochs=50)
    train_loss43, recoProb43 = model400.reconstruct(teste4)
    threshold43 = np.mean(train_loss43.detach().numpy()) + np.std(train_loss43.detach().numpy())
    print("Threshold: ", threshold43)
    reconstructions43 = torch.bernoulli(recoProb43)
    preds43 = predict(train_loss43.detach().numpy(), reconstructions43.detach().numpy(), threshold43, test_data4)
    print_stats(preds43.numpy(), test_labelsb4) 
    valores.append([threshold43, format(accuracy_score(preds43.numpy(), test_labelsb4)), format(precision_score(preds43.numpy(), test_labelsb4)), format(recall_score(preds43.numpy(), test_labelsb4))])
    
for x in range(10):
    mse44, pl44 = model200.fit(dataset4, batch_size=10, epochs=50)
    train_loss44, recoProb44 = model400.reconstruct(teste4)
    threshold44 = np.mean(train_loss44.detach().numpy()) + np.std(train_loss44.detach().numpy())
    print("Threshold: ", threshold44)
    reconstructions44 = torch.bernoulli(recoProb44)
    preds44 = predict(train_loss44.detach().numpy(), reconstructions44.detach().numpy(), threshold44, test_data4)
    print_stats(preds44.numpy(), test_labelsb4) 
    valores.append([threshold44, format(accuracy_score(preds44.numpy(), test_labelsb4)), format(precision_score(preds44.numpy(), test_labelsb4)), format(recall_score(preds44.numpy(), test_labelsb4))])
    
for x in range(10):
    mse45, pl45 = model400.fit(dataset4, batch_size=10, epochs=100)
    train_loss45, recoProb45 = model400.reconstruct(teste4)
    threshold45 = np.mean(train_loss45.detach().numpy()) + np.std(train_loss45.detach().numpy())
    print("Threshold: ", threshold45)
    reconstructions45 = torch.bernoulli(recoProb45)
    preds45 = predict(train_loss45.detach().numpy(), reconstructions45.detach().numpy(), threshold45, test_data4)
    print_stats(preds45.numpy(), test_labelsb4) 
    valores.append([threshold45, format(accuracy_score(preds45.numpy(), test_labelsb4)), format(precision_score(preds45.numpy(), test_labelsb4)), format(recall_score(preds45.numpy(), test_labelsb4))])
    
for x in range(10):
    mse46, pl46 = model200.fit(dataset4, batch_size=10, epochs=100)
    train_loss46, recoProb46 = model400.reconstruct(teste4)
    threshold46 = np.mean(train_loss46.detach().numpy()) + np.std(train_loss46.detach().numpy())
    print("Threshold: ", threshold46)
    reconstructions46 = torch.bernoulli(recoProb46)
    preds46 = predict(train_loss46.detach().numpy(), reconstructions46.detach().numpy(), threshold46, test_data4)
    print_stats(preds46.numpy(), test_labelsb4) 
    valores.append([threshold46, format(accuracy_score(preds46.numpy(), test_labelsb4)), format(precision_score(preds46.numpy(), test_labelsb4)), format(recall_score(preds46.numpy(), test_labelsb4))])
    
df = pd.DataFrame(valores) 
df.to_csv('resultRBM800norm.csv',index=False)

def create_download_link(title = "Download CSV file", filename = "data.csv"):  
    html = '<a href={filename}>{title}</a>'
    html = html.format(title=title,filename=filename)
    return HTML(html)

# create a link to download the dataframe which was saved with .to_csv method
create_download_link(filename='resultRBM800norm.csv')
    

In [7]:
#CARREGAR KDD99 - 1300 - MINMAX
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

#carregar os dados 
dataframe5 = pd.read_csv("/kaggle/input/kdd991300mm/data1300kddDICMinMax.csv", header=None)

#pegar valores da dataframe
raw_data5 = dataframe5.values
dataframe5.head()

# Separar labels
labels5 = raw_data5[1:, -1]

# Separar valores
data5 = raw_data5[1:, 0:41]

# Dividir os dados nos sets
train_data5, test_data5, train_labels5, test_labels5 = train_test_split(
        data5, labels5, test_size=0.2, random_state=21
)

# Transformar valores de texto para número
train_labels5 = np.float32(train_labels5)
test_labels5 = np.float32(test_labels5)
test_data5 = np.float32(test_data5)
train_labelsb5 = train_labels5.astype(bool)
test_labelsb5 = test_labels5.astype(bool)
normal_train_data5 = np.float32(train_data5[~train_labelsb5]) #dados (false) normais (0)
normal_test_data5 = np.float32(test_data5[~test_labelsb5])
anomalous_train_data5 = np.float32(train_data5[train_labelsb5]) #dados (true) anomalos (1)
anomalous_test_data5 = np.float32(test_data5[test_labelsb5])
normal_train_labels5 = np.float32(train_labels5[~train_labelsb5])

dataset5=Dataset(normal_train_data5, normal_train_labels5)
teste5=Dataset(test_data5, test_labels5)

/kaggle/input/kdd99800mm/data800kddDICMinMax.csv
/kaggle/input/kdd991300norm/data1300kddDICnormalized.csv
/kaggle/input/kdd991300mm/data1300kddDICMinMax.csv
/kaggle/input/kdd99400norm/data400kddDICnormalized.csv
/kaggle/input/kdd99400mm/data400kddDICMinMax.csv
/kaggle/input/kdd99800norm/data800kddDICnormalized.csv
/kaggle/input/kdd995000mm/data5000kddDICMinMax.csv
2023-01-02 16:47:56,188 - learnergy.core.dataset — INFO — Creating class: Dataset.
2023-01-02 16:47:56,189 - learnergy.core.dataset — INFO — Class created.
2023-01-02 16:47:56,190 - learnergy.core.dataset — DEBUG — Data: (204, 41) | Targets: (204,) | Transforms: None.
2023-01-02 16:47:56,192 - learnergy.core.dataset — INFO — Creating class: Dataset.
2023-01-02 16:47:56,193 - learnergy.core.dataset — INFO — Class created.
2023-01-02 16:47:56,194 - learnergy.core.dataset — DEBUG — Data: (261, 41) | Targets: (261,) | Transforms: None.


In [ ]:
valores=[["MSE", "PL", 'RMSE', 'PV']]
valores.append(["kdd1300MinMax"])
for x in range(10):
    mse51, pl51 = model400.fit(dataset5, batch_size=50, epochs=50)
    train_loss51, recoProb51 = model400.reconstruct(teste5)
    threshold51 = np.mean(train_loss51.detach().numpy()) + np.std(train_loss51.detach().numpy())
    print("Threshold: ", threshold51)
    reconstructions51 = torch.bernoulli(recoProb51)
    preds51 = predict(train_loss51.detach().numpy(), reconstructions51.detach().numpy(), threshold51, test_data5)
    print_stats(preds51.numpy(), test_labelsb5) 
    valores.append([threshold51, format(accuracy_score(preds51.numpy(), test_labelsb5)), format(precision_score(preds51.numpy(), test_labelsb5)), format(recall_score(preds51.numpy(), test_labelsb5))])
     
for x in range(10):
    mse52, pl52 = model200.fit(dataset5, batch_size=50, epochs=50)
    train_loss52, recoProb52 = model400.reconstruct(teste5)
    threshold52 = np.mean(train_loss52.detach().numpy()) + np.std(train_loss52.detach().numpy())
    print("Threshold: ", threshold52)
    reconstructions52 = torch.bernoulli(recoProb52)
    preds52 = predict(train_loss52.detach().numpy(), reconstructions52.detach().numpy(), threshold52, test_data5)
    print_stats(preds52.numpy(), test_labelsb5) 
    valores.append([threshold52, format(accuracy_score(preds52.numpy(), test_labelsb5)), format(precision_score(preds52.numpy(), test_labelsb5)), format(recall_score(preds52.numpy(), test_labelsb5))])
    
for x in range(10):
    mse53, pl53 = model400.fit(dataset5, batch_size=10, epochs=50)
    train_loss53, recoProb53 = model400.reconstruct(teste5)
    threshold53 = np.mean(train_loss53.detach().numpy()) + np.std(train_loss53.detach().numpy())
    print("Threshold: ", threshold53)
    reconstructions53 = torch.bernoulli(recoProb53)
    preds53 = predict(train_loss53.detach().numpy(), reconstructions53.detach().numpy(), threshold53, test_data5)
    print_stats(preds53.numpy(), test_labelsb5) 
    valores.append([threshold53, format(accuracy_score(preds53.numpy(), test_labelsb5)), format(precision_score(preds53.numpy(), test_labelsb5)), format(recall_score(preds53, test_labelsb5))])
     
for x in range(10):
    mse54, pl54 = model200.fit(dataset5, batch_size=10, epochs=50)
    train_loss54, recoProb54 = model400.reconstruct(teste5)
    threshold54 = np.mean(train_loss54.detach().numpy()) + np.std(train_loss54.detach().numpy())
    print("Threshold: ", threshold54)
    reconstructions54 = torch.bernoulli(recoProb54)
    preds54 = predict(train_loss54.detach().numpy(), reconstructions54.detach().numpy(), threshold54, test_data5)
    print_stats(preds54.numpy(), test_labelsb5) 
    valores.append([threshold54, format(accuracy_score(preds54.numpy(), test_labelsb5)), format(precision_score(preds54.numpy(), test_labelsb5)), format(recall_score(preds54, test_labelsb5))])
    
for x in range(10):
    mse55, pl55 = model400.fit(dataset5, batch_size=10, epochs=100)
    train_loss55, recoProb55 = model400.reconstruct(teste5)
    threshold55 = np.mean(train_loss55.detach().numpy()) + np.std(train_loss55.detach().numpy())
    print("Threshold: ", threshold55)
    reconstructions55 = torch.bernoulli(recoProb55)
    preds55 = predict(train_loss55.detach().numpy(), reconstructions55.detach().numpy(), threshold55, test_data5)
    print_stats(preds55.numpy(), test_labelsb5) 
    valores.append([threshold55, format(accuracy_score(preds55.numpy(), test_labelsb5)), format(precision_score(preds55.numpy(), test_labelsb5)), format(recall_score(preds55.numpy(), test_labelsb5))])
    
for x in range(10):
    mse56, pl56 = model200.fit(dataset5, batch_size=10, epochs=100)
    train_loss56, recoProb56 = model400.reconstruct(teste5)
    threshold56 = np.mean(train_loss56.detach().numpy()) + np.std(train_loss56.detach().numpy())
    print("Threshold: ", threshold56)
    reconstructions56 = torch.bernoulli(recoProb56)
    preds56 = predict(train_loss56.detach().numpy(), reconstructions56.detach().numpy(), threshold56, test_data5)
    print_stats(preds56.numpy(), test_labelsb5) 
    valores.append([threshold56, format(accuracy_score(preds56.numpy(), test_labelsb5)), format(precision_score(preds56.numpy(), test_labelsb5)), format(recall_score(preds56.numpy(), test_labelsb5))])
    
df = pd.DataFrame(valores) 
df.to_csv('resultRBM1300mm.csv',index=False)

def create_download_link(title = "Download CSV file", filename = "data.csv"):  
    html = '<a href={filename}>{title}</a>'
    html = html.format(title=title,filename=filename)
    return HTML(html)

# create a link to download the dataframe which was saved with .to_csv method
create_download_link(filename='resultRBM1300mm.csv')

2023-01-02 16:48:02,247 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 1/50


100%|██████████| 5/5 [00:00<00:00, 186.37it/s]

2023-01-02 16:48:02,281 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 2.719177 | log-PL: -21.422972
2023-01-02 16:48:02,282 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 2/50



100%|██████████| 5/5 [00:00<00:00, 265.22it/s]

2023-01-02 16:48:02,306 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 1.707364 | log-PL: -21.295256
2023-01-02 16:48:02,307 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 3/50


...

2023-01-02 16:48:16,531 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 1.795238 | log-PL: -21.815155
2023-01-02 16:48:16,533 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 5/50



100%|██████████| 5/5 [00:00<00:00, 232.42it/s]

2023-01-02 16:48:16,559 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 1.634722 | log-PL: -21.633091
2023-01-02 16:48:16,561 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 6/50



100%|██████████| 5/5 [00:00<00:00, 247.66it/s]

2023-01-02 16:48:16,586 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 1.762220 | log-PL: -21.505814
2023-01-02 16:48:16,587 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 7/50


In [10]:
#CARREGAR KDD99 - 1300 - NORMALIZED
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

#carregar os dados 
dataframe6 = pd.read_csv("/kaggle/input/kdd991300norm/data1300kddDICnormalized.csv", header=None)

#pegar valores da dataframe
raw_data6 = dataframe6.values
dataframe6.head()

# Separar labels
labels6 = raw_data6[1:, -1]

# Separar valores
data6 = raw_data6[1:, 0:41]

# Dividir os dados nos sets
train_data6, test_data6, train_labels6, test_labels6 = train_test_split(
        data6, labels6, test_size=0.2, random_state=21
)

# Transformar valores de texto para número
train_labels6 = np.float32(train_labels6)
test_labels6 = np.float32(test_labels6)
test_data6 = np.float32(test_data6)
train_labelsb6 = train_labels6.astype(bool)
test_labelsb6 = test_labels6.astype(bool)
normal_train_data6 = np.float32(train_data6[~train_labelsb6]) #dados (false) normais (0)
normal_test_data6 = np.float32(test_data6[~test_labelsb6])
anomalous_train_data6 = np.float32(train_data6[train_labelsb6]) #dados (true) anomalos (1)
anomalous_test_data6 = np.float32(test_data6[test_labelsb6])
normal_train_labels6 = np.float32(train_labels6[~train_labelsb6])

dataset6=Dataset(normal_train_data6, normal_train_labels6)
teste6=Dataset(test_data6, test_labels6)

/kaggle/input/kdd99800mm/data800kddDICMinMax.csv
/kaggle/input/kdd991300norm/data1300kddDICnormalized.csv
/kaggle/input/kdd991300mm/data1300kddDICMinMax.csv
/kaggle/input/kdd99400norm/data400kddDICnormalized.csv
/kaggle/input/kdd99400mm/data400kddDICMinMax.csv
/kaggle/input/kdd99800norm/data800kddDICnormalized.csv
/kaggle/input/kdd995000mm/data5000kddDICMinMax.csv
2023-01-02 16:59:14,469 - learnergy.core.dataset — INFO — Creating class: Dataset.
2023-01-02 16:59:14,470 - learnergy.core.dataset — INFO — Class created.
2023-01-02 16:59:14,474 - learnergy.core.dataset — DEBUG — Data: (204, 41) | Targets: (204,) | Transforms: None.
2023-01-02 16:59:14,476 - learnergy.core.dataset — INFO — Creating class: Dataset.
2023-01-02 16:59:14,477 - learnergy.core.dataset — INFO — Class created.
2023-01-02 16:59:14,478 - learnergy.core.dataset — DEBUG — Data: (261, 41) | Targets: (261,) | Transforms: None.


In [11]:
valores=[["MSE", "PL", 'RMSE', 'PV']]
valores.append(["kdd1300Normal"])
for x in range(10):
    mse61, pl61 = model400.fit(dataset6, batch_size=50, epochs=50)
    train_loss61, recoProb61 = model400.reconstruct(teste6)
    threshold61 = np.mean(train_loss61.detach().numpy()) + np.std(train_loss61.detach().numpy())
    print("Threshold: ", threshold61)
    reconstructions61 = torch.bernoulli(recoProb61)
    preds61 = predict(train_loss61.detach().numpy(), reconstructions61.detach().numpy(), threshold61, test_data6)
    print_stats(preds61.numpy(), test_labelsb6) 
    valores.append([threshold61, format(accuracy_score(preds61.numpy(), test_labelsb6)), format(precision_score(preds61.numpy(), test_labelsb6)), format(recall_score(preds61.numpy(), test_labelsb6))])
    
for x in range(10):
    mse62, pl62 = model200.fit(dataset6, batch_size=50, epochs=50)
    train_loss62, recoProb62 = model400.reconstruct(teste6)
    threshold62 = np.mean(train_loss62.detach().numpy()) + np.std(train_loss62.detach().numpy())
    print("Threshold: ", threshold62)
    reconstructions62 = torch.bernoulli(recoProb62)
    preds62 = predict(train_loss62.detach().numpy(), reconstructions62.detach().numpy(), threshold62, test_data6)
    print_stats(preds62.numpy(), test_labelsb6) 
    valores.append([threshold62, format(accuracy_score(preds62.numpy(), test_labelsb6)), format(precision_score(preds62.numpy(), test_labelsb6)), format(recall_score(preds62.numpy(), test_labelsb6))])
    
for x in range(10):
    mse63, pl63 = model400.fit(dataset6, batch_size=10, epochs=50)
    train_loss63, recoProb63 = model400.reconstruct(teste6)
    threshold63 = np.mean(train_loss63.detach().numpy()) + np.std(train_loss63.detach().numpy())
    print("Threshold: ", threshold63)
    reconstructions63 = torch.bernoulli(recoProb63)
    preds63 = predict(train_loss63.detach().numpy(), reconstructions63.detach().numpy(), threshold63, test_data6)
    print_stats(preds63.numpy(), test_labelsb6) 
    valores.append([threshold63, format(accuracy_score(preds63.numpy(), test_labelsb6)), format(precision_score(preds63.numpy(), test_labelsb6)), format(recall_score(preds63.numpy(), test_labelsb6))])
    
for x in range(10):
    mse64, pl64 = model200.fit(dataset6, batch_size=10, epochs=50)
    train_loss64, recoProb64 = model400.reconstruct(teste6)
    threshold64 = np.mean(train_loss64.detach().numpy()) + np.std(train_loss64.detach().numpy())
    print("Threshold: ", threshold64)
    reconstructions64 = torch.bernoulli(recoProb64)
    preds64 = predict(train_loss64.detach().numpy(), reconstructions64.detach().numpy(), threshold64, test_data6)
    print_stats(preds64.numpy(), test_labelsb6) 
    valores.append([threshold64, format(accuracy_score(preds64.numpy(), test_labelsb6)), format(precision_score(preds64.numpy(), test_labelsb6)), format(recall_score(preds64.numpy(), test_labelsb6))])
    
for x in range(10):
    mse65, pl65 = model400.fit(dataset6, batch_size=10, epochs=100)
    train_loss65, recoProb65 = model400.reconstruct(teste6)
    threshold65 = np.mean(train_loss65.detach().numpy()) + np.std(train_loss65.detach().numpy())
    print("Threshold: ", threshold65)
    reconstructions65 = torch.bernoulli(recoProb65)
    preds65 = predict(train_loss65.detach().numpy(), reconstructions65.detach().numpy(), threshold65, test_data6)
    print_stats(preds65.numpy(), test_labelsb6) 
    valores.append([threshold65, format(accuracy_score(preds65.numpy(), test_labelsb6)), format(precision_score(preds65.numpy(), test_labelsb6)), format(recall_score(preds65.numpy(), test_labelsb6))])
    
for x in range(10):
    mse66, pl66 = model200.fit(dataset6, batch_size=10, epochs=100)
    train_loss66, recoProb66 = model400.reconstruct(teste6)
    threshold66 = np.mean(train_loss66.detach().numpy()) + np.std(train_loss66.detach().numpy())
    print("Threshold: ", threshold66)
    reconstructions66 = torch.bernoulli(recoProb66)
    preds66 = predict(train_loss66.detach().numpy(), reconstructions66.detach().numpy(), threshold66, test_data6)
    print_stats(preds66.numpy(), test_labelsb6) 
    valores.append([threshold66, format(accuracy_score(preds66.numpy(), test_labelsb6)), format(precision_score(preds66.numpy(), test_labelsb6)), format(recall_score(preds66.numpy(), test_labelsb6))])

df = pd.DataFrame(valores) 
df.to_csv('resultRBM1300norm.csv',index=False)

def create_download_link(title = "Download CSV file", filename = "data.csv"):  
    html = '<a href={filename}>{title}</a>'
    html = html.format(title=title,filename=filename)
    return HTML(html)

# create a link to download the dataframe which was saved with .to_csv method
create_download_link(filename='resultRBM1300norm.csv')

2023-01-02 16:59:19,274 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 1/50


100%|██████████| 5/5 [00:00<00:00, 206.70it/s]

2023-01-02 16:59:19,304 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 1.950309 | log-PL: -19.819214
2023-01-02 16:59:19,306 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 2/50



100%|██████████| 5/5 [00:00<00:00, 247.81it/s]

2023-01-02 16:59:19,332 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 1.175479 | log-PL: -19.931974
2023-01-02 16:59:19,333 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 3/50


...


100%|██████████| 21/21 [00:00<00:00, 470.78it/s]

2023-01-02 17:02:48,634 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 0.155524 | log-PL: -19.625046
2023-01-02 17:02:48,635 - learnergy.models.gaussian.gaussian_rbm — INFO — Reconstructing new samples ...



100%|██████████| 1/1 [00:00<00:00, 172.39it/s]

2023-01-02 17:02:48,648 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 0.168464
Threshold:  0.16846426
Accuracy = 0.16475095785440613
Precision = 0.0
Recall = 0.0



/opt/conda/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 due to no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [12]:
#CARREGAR KDD99 - 5000 - MINMAX
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

#carregar os dados 
dataframe7 = pd.read_csv("/kaggle/input/kdd995000mm/data5000kddDICMinMax.csv", header=None)

#pegar valores da dataframe
raw_data7 = dataframe7.values
dataframe7.head()

# Separar labels
labels7 = raw_data7[1:, -1]

# Separar valores
data7 = raw_data7[1:, 0:41]

# Dividir os dados nos sets
train_data7, test_data7, train_labels7, test_labels7 = train_test_split(
        data7, labels7, test_size=0.2, random_state=21
)

# Transformar valores de texto para número
train_labels7 = np.float32(train_labels7)
test_labels7 = np.float32(test_labels7)
test_data7 = np.float32(test_data7)
train_labelsb7 = train_labels7.astype(bool)
test_labelsb7 = test_labels7.astype(bool)
normal_train_data7 = np.float32(train_data7[~train_labelsb7]) #dados (false) normais (0)
normal_test_data7 = np.float32(test_data7[~test_labelsb7])
anomalous_train_data7 = np.float32(train_data7[train_labelsb7]) #dados (true) anomalos (1)
anomalous_test_data7 = np.float32(test_data7[test_labelsb7])
normal_train_labels7 = np.float32(train_labels7[~train_labelsb7])

dataset7=Dataset(normal_train_data7, normal_train_labels7)
teste7=Dataset(test_data7, test_labels7)

/kaggle/input/kdd99800mm/data800kddDICMinMax.csv
/kaggle/input/kdd991300norm/data1300kddDICnormalized.csv
/kaggle/input/kdd991300mm/data1300kddDICMinMax.csv
/kaggle/input/kdd99400norm/data400kddDICnormalized.csv
/kaggle/input/kdd99400mm/data400kddDICMinMax.csv
/kaggle/input/kdd99800norm/data800kddDICnormalized.csv
/kaggle/input/kdd995000mm/data5000kddDICMinMax.csv
2023-01-02 17:29:55,068 - learnergy.core.dataset — INFO — Creating class: Dataset.
2023-01-02 17:29:55,069 - learnergy.core.dataset — INFO — Class created.
2023-01-02 17:29:55,071 - learnergy.core.dataset — DEBUG — Data: (784, 41) | Targets: (784,) | Transforms: None.
2023-01-02 17:29:55,072 - learnergy.core.dataset — INFO — Creating class: Dataset.
2023-01-02 17:29:55,073 - learnergy.core.dataset — INFO — Class created.
2023-01-02 17:29:55,074 - learnergy.core.dataset — DEBUG — Data: (1000, 41) | Targets: (1000,) | Transforms: None.


In [13]:
valores=[["MSE", "PL", 'RMSE', 'PV']]
valores.append(["kdd5000MinMax"])
for x in range(10):
    mse71, pl71 = model400.fit(dataset7, batch_size=50, epochs=50)
    train_loss71, recoProb71 = model400.reconstruct(teste7)
    threshold71 = np.mean(train_loss71.detach().numpy()) + np.std(train_loss71.detach().numpy())
    print("Threshold: ", threshold71)
    reconstructions71 = torch.bernoulli(recoProb71)
    preds71 = predict(train_loss71.detach().numpy(), reconstructions71.detach().numpy(), threshold71, test_data7)
    print_stats(preds71.numpy(), test_labelsb7) 
    valores.append([threshold71, format(accuracy_score(preds71.numpy(), test_labelsb7)), format(precision_score(preds71.numpy(), test_labelsb7)), format(recall_score(preds71.numpy(), test_labelsb7))])
    
for x in range(10):
    mse72, pl72= model200.fit(dataset7, batch_size=50, epochs=50)
    train_loss72, recoProb72 = model400.reconstruct(teste7)
    threshold72 = np.mean(train_loss72.detach().numpy()) + np.std(train_loss72.detach().numpy())
    print("Threshold: ", threshold72)
    reconstructions72 = torch.bernoulli(recoProb72)
    preds72 = predict(train_loss72.detach().numpy(), reconstructions72.detach().numpy(), threshold72, test_data7)
    print_stats(preds72.numpy(), test_labelsb7) 
    valores.append([threshold72, format(accuracy_score(preds72.numpy(), test_labelsb7)), format(precision_score(preds72.numpy(), test_labelsb7)), format(recall_score(preds72.numpy(), test_labelsb7))])
    
for x in range(10):
    mse73, pl73 = model400.fit(dataset7, batch_size=10, epochs=50)
    train_loss73, recoProb73 = model400.reconstruct(teste7)
    threshold73 = np.mean(train_loss73.detach().numpy()) + np.std(train_loss73.detach().numpy())
    print("Threshold: ", threshold73)
    reconstructions73 = torch.bernoulli(recoProb73)
    preds73 = predict(train_loss73.detach().numpy(), reconstructions73.detach().numpy(), threshold73, test_data7)
    print_stats(preds73.numpy(), test_labelsb7) 
    valores.append([threshold73, format(accuracy_score(preds73.numpy(), test_labelsb7)), format(precision_score(preds73.numpy(), test_labelsb7)), format(recall_score(preds73.numpy(), test_labelsb7))])
    
for x in range(10):
    mse74, pl74 = model200.fit(dataset7, batch_size=10, epochs=50)
    train_loss74, recoProb74 = model400.reconstruct(teste7)
    threshold74 = np.mean(train_loss74.detach().numpy()) + np.std(train_loss74.detach().numpy())
    print("Threshold: ", threshold74)
    reconstructions74 = torch.bernoulli(recoProb74)
    preds74 = predict(train_loss74.detach().numpy(), reconstructions74.detach().numpy(), threshold74, test_data7)
    print_stats(preds74.numpy(), test_labelsb7) 
    valores.append([threshold74, format(accuracy_score(preds74.numpy(), test_labelsb7)), format(precision_score(preds74.numpy(), test_labelsb7)), format(recall_score(preds74.numpy(), test_labelsb7))])
    
for x in range(10):
    mse75, pl75 = model400.fit(dataset7, batch_size=10, epochs=100)
    train_loss75, recoProb75 = model400.reconstruct(teste7)
    threshold75 = np.mean(train_loss75.detach().numpy()) + np.std(train_loss75.detach().numpy())
    print("Threshold: ", threshold75)
    reconstructions75 = torch.bernoulli(recoProb75)
    preds75 = predict(train_loss75.detach().numpy(), reconstructions75.detach().numpy(), threshold75, test_data7)
    print_stats(preds75.numpy(), test_labelsb7) 
    valores.append([threshold75, format(accuracy_score(preds75.numpy(), test_labelsb7)), format(precision_score(preds75.numpy(), test_labelsb7)), format(recall_score(preds75.numpy(), test_labelsb7))])
    
for x in range(10):
    mse76, pl76 = model200.fit(dataset7, batch_size=10, epochs=100)
    train_loss76, recoProb76 = model400.reconstruct(teste7)
    threshold76 = np.mean(train_loss76.detach().numpy()) + np.std(train_loss76.detach().numpy())
    print("Threshold: ", threshold76)
    reconstructions76 = torch.bernoulli(recoProb76)
    preds76 = predict(train_loss76.detach().numpy(), reconstructions76.detach().numpy(), threshold76, test_data7)
    print_stats(preds76.numpy(), test_labelsb7) 
    valores.append([threshold76, format(accuracy_score(preds76.numpy(), test_labelsb7)), format(precision_score(preds76.numpy(), test_labelsb7)), format(recall_score(preds76.numpy(), test_labelsb7))])
    
    
df = pd.DataFrame(valores) 
df.to_csv('resultadosRBM5000mm.csv',index=False)

def create_download_link(title = "Download CSV file", filename = "data.csv"):  
    html = '<a href={filename}>{title}</a>'
    html = html.format(title=title,filename=filename)
    return HTML(html)

# create a link to download the dataframe which was saved with .to_csv method
create_download_link(filename='resultadosRBM5000mm.csv')

2023-01-02 17:30:00,659 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 1/50


100%|██████████| 16/16 [00:00<00:00, 240.92it/s]

2023-01-02 17:30:00,734 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 1.507158 | log-PL: -21.119804
2023-01-02 17:30:00,736 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 2/50



100%|██████████| 16/16 [00:00<00:00, 235.47it/s]

2023-01-02 17:30:00,810 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 1.245729 | log-PL: -20.992535
2023-01-02 17:30:00,811 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 3/50


...

2023-01-02 17:41:10,605 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 1.507862 | log-PL: -20.770447
2023-01-02 17:41:10,606 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 100/100



100%|██████████| 79/79 [00:00<00:00, 453.28it/s]

2023-01-02 17:41:10,786 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 1.477307 | log-PL: -20.611130
2023-01-02 17:41:10,788 - learnergy.models.gaussian.gaussian_rbm — INFO — Reconstructing new samples ...



100%|██████████| 1/1 [00:00<00:00, 59.66it/s]


2023-01-02 17:41:10,811 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 5.566530
Threshold:  5.5665298
Accuracy = 0.801
Precision = 0.801
Recall = 1.0


In [15]:
#CARREGAR KDD99 - 5000 - NORMALIZED
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

#carregar os dados 
dataframe8 = pd.read_csv("/kaggle/input/kdd995000norm/data5000kddDICnormalized.csv", header=None)

#pegar valores da dataframe
raw_data8 = dataframe8.values
dataframe8.head()

# Separar labels
labels8 = raw_data8[1:, -1]

# Separar valores
data8 = raw_data8[1:, 0:41]

# Dividir os dados nos sets
train_data8, test_data8, train_labels8, test_labels8 = train_test_split(
        data8, labels8, test_size=0.2, random_state=21
)

# Transformar valores de texto para número
train_labels8 = np.float32(train_labels8)
test_labels8 = np.float32(test_labels8)
test_data8 = np.float32(test_data8)
train_labelsb8 = train_labels8.astype(bool)
test_labelsb8 = test_labels8.astype(bool)
normal_train_data8 = np.float32(train_data8[~train_labelsb8]) #dados (false) normais (0)
normal_test_data8 = np.float32(test_data8[~test_labelsb8])
anomalous_train_data8 = np.float32(train_data8[train_labelsb8]) #dados (true) anomalos (1)
anomalous_test_data8 = np.float32(test_data8[test_labelsb8])
normal_train_labels8 = np.float32(train_labels8[~train_labelsb8])

dataset8=Dataset(normal_train_data8, normal_train_labels8)
teste8=Dataset(test_data8, test_labels8)

/kaggle/input/kdd99800mm/data800kddDICMinMax.csv
/kaggle/input/kdd991300norm/data1300kddDICnormalized.csv
/kaggle/input/kdd991300mm/data1300kddDICMinMax.csv
/kaggle/input/kdd99400norm/data400kddDICnormalized.csv
/kaggle/input/kdd99400mm/data400kddDICMinMax.csv
/kaggle/input/kdd995000norm/data5000kddDICnormalized.csv
/kaggle/input/kdd99800norm/data800kddDICnormalized.csv
/kaggle/input/kdd995000mm/data5000kddDICMinMax.csv
2023-01-02 17:47:12,285 - learnergy.core.dataset — INFO — Creating class: Dataset.
2023-01-02 17:47:12,286 - learnergy.core.dataset — INFO — Class created.
2023-01-02 17:47:12,289 - learnergy.core.dataset — DEBUG — Data: (784, 41) | Targets: (784,) | Transforms: None.
2023-01-02 17:47:12,291 - learnergy.core.dataset — INFO — Creating class: Dataset.
2023-01-02 17:47:12,292 - learnergy.core.dataset — INFO — Class created.
2023-01-02 17:47:12,294 - learnergy.core.dataset — DEBUG — Data: (1000, 41) | Targets: (1000,) | Transforms: None.


In [16]:
valores=[["MSE", "PL", 'RMSE', 'PV']]
valores.append(["kdd5000Normal"])
for x in range(10):
    mse81, pl81 = model400.fit(dataset8, batch_size=50, epochs=50)
    train_loss81, recoProb81 = model400.reconstruct(teste8)
    threshold81 = np.mean(train_loss81.detach().numpy()) + np.std(train_loss81.detach().numpy())
    print("Threshold: ", threshold81)
    reconstructions81 = torch.bernoulli(recoProb81)
    preds81 = predict(train_loss81.detach().numpy(), reconstructions81.detach().numpy(), threshold81, test_data8)
    print_stats(preds81.numpy(), test_labelsb8) 
    valores.append([threshold81, format(accuracy_score(preds81.numpy(), test_labelsb8)), format(precision_score(preds81.numpy(), test_labelsb8)), format(recall_score(preds81.numpy(), test_labelsb8))])
    
for x in range(10):
    mse82, pl82= model200.fit(dataset8, batch_size=50, epochs=50)
    train_loss82, recoProb82 = model400.reconstruct(teste8)
    threshold82 = np.mean(train_loss82.detach().numpy()) + np.std(train_loss82.detach().numpy())
    print("Threshold: ", threshold82)
    reconstructions82 = torch.bernoulli(recoProb82)
    preds82 = predict(train_loss82.detach().numpy(), reconstructions82.detach().numpy(), threshold82, test_data8)
    print_stats(preds82.numpy(), test_labelsb8) 
    valores.append([threshold82, format(accuracy_score(preds82.numpy(), test_labelsb8)), format(precision_score(preds82.numpy(), test_labelsb8)), format(recall_score(preds82.numpy(), test_labelsb8))])
    
for x in range(10):
    mse83, pl83 = model400.fit(dataset8, batch_size=10, epochs=50)
    train_loss83, recoProb83 = model400.reconstruct(teste8)
    threshold83 = np.mean(train_loss83.detach().numpy()) + np.std(train_loss83.detach().numpy())
    print("Threshold: ", threshold83)
    reconstructions83 = torch.bernoulli(recoProb83)
    preds83 = predict(train_loss83.detach().numpy(), reconstructions83.detach().numpy(), threshold83, test_data8)
    print_stats(preds83.numpy(), test_labelsb8) 
    valores.append([threshold83, format(accuracy_score(preds83.numpy(), test_labelsb8)), format(precision_score(preds83.numpy(), test_labelsb8)), format(recall_score(preds83.numpy(), test_labelsb8))])
    
for x in range(10):
    mse84, pl84 = model200.fit(dataset8, batch_size=10, epochs=50)
    train_loss84, recoProb84 = model400.reconstruct(teste8)
    threshold84 = np.mean(train_loss84.detach().numpy()) + np.std(train_loss84.detach().numpy())
    print("Threshold: ", threshold84)
    reconstructions84 = torch.bernoulli(recoProb84)
    preds84 = predict(train_loss84.detach().numpy(), reconstructions84.detach().numpy(), threshold84, test_data8)
    print_stats(preds84.numpy(), test_labelsb8) 
    valores.append([threshold84, format(accuracy_score(preds84.numpy(), test_labelsb8)), format(precision_score(preds84.numpy(), test_labelsb8)), format(recall_score(preds84.numpy(), test_labelsb8))])
    
for x in range(10):
    mse85, pl85 = model400.fit(dataset8, batch_size=10, epochs=100)
    train_loss85, recoProb85 = model400.reconstruct(teste8)
    threshold85 = np.mean(train_loss85.detach().numpy()) + np.std(train_loss85.detach().numpy())
    print("Threshold: ", threshold85)
    reconstructions85 = torch.bernoulli(recoProb85)
    preds85 = predict(train_loss85.detach().numpy(), reconstructions85.detach().numpy(), threshold85, test_data8)
    print_stats(preds85.numpy(), test_labelsb8) 
    valores.append([threshold85, format(accuracy_score(preds85.numpy(), test_labelsb8)), format(precision_score(preds85.numpy(), test_labelsb8)), format(recall_score(preds85.numpy(), test_labelsb8))])
    
for x in range(10):
    mse86, pl86 = model200.fit(dataset8, batch_size=10, epochs=100)
    train_loss86, recoProb86 = model400.reconstruct(teste8)
    threshold86 = np.mean(train_loss86.detach().numpy()) + np.std(train_loss86.detach().numpy())
    print("Threshold: ", threshold86)
    reconstructions86 = torch.bernoulli(recoProb86)
    preds86 = predict(train_loss86.detach().numpy(), reconstructions86.detach().numpy(), threshold86, test_data8)
    print_stats(preds86.numpy(), test_labelsb8) 
    valores.append([threshold86, format(accuracy_score(preds86.numpy(), test_labelsb8)), format(precision_score(preds86.numpy(), test_labelsb8)), format(recall_score(preds86.numpy(), test_labelsb8))])
    
    
df = pd.DataFrame(valores) 
df.to_csv('resultadosRBM5000norm.csv',index=False)

def create_download_link(title = "Download CSV file", filename = "data.csv"):  
    html = '<a href={filename}>{title}</a>'
    html = html.format(title=title,filename=filename)
    return HTML(html)

# create a link to download the dataframe which was saved with .to_csv method
create_download_link(filename='resultadosRBM5000norm.csv')

2023-01-02 17:47:17,926 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 1/50


100%|██████████| 16/16 [00:00<00:00, 239.45it/s]

2023-01-02 17:47:17,998 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 1.522502 | log-PL: -19.793455
2023-01-02 17:47:18,000 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 2/50



100%|██████████| 16/16 [00:00<00:00, 243.89it/s]

2023-01-02 17:47:18,070 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 1.296514 | log-PL: -19.768393
2023-01-02 17:47:18,072 - learnergy.models.gaussian.gaussian_rbm — INFO — Epoch 3/50


...


100%|██████████| 79/79 [00:00<00:00, 321.46it/s]

2023-01-02 17:58:31,848 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 0.063291 | log-PL: -19.525698
2023-01-02 17:58:31,850 - learnergy.models.gaussian.gaussian_rbm — INFO — Reconstructing new samples ...



100%|██████████| 1/1 [00:00<00:00, 63.37it/s]

2023-01-02 17:58:31,870 - learnergy.models.gaussian.gaussian_rbm — INFO — MSE: 0.071329
Threshold:  0.07132917
Accuracy = 0.199
Precision = 0.0
Recall = 0.0



/opt/conda/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/opt/conda/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 due to no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
